In [1]:
%load_ext autoreload
%autoreload 2

%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
from PIL import Image
import torch.nn.functional as F
import torch
from torch import nn
from torchsummary import summary
from importlib.util import find_spec
if find_spec("text_recognizer") is None:
    import sys
    sys.path.append('..')

In [1]:
from omegaconf import OmegaConf

In [6]:
path = "../training/experiments/image_transformer.yaml"

In [7]:
conf = OmegaConf.load(path)

In [11]:
print(OmegaConf.to_yaml(conf))

network:
  type: ImageTransformer
  args:
    input_shape: None
    output_shape: None
    encoder:
      type: None
      args: None
    mapping: sentence_piece
    num_decoder_layers: 4
    hidden_dim: 256
    num_heads: 4
    expansion_dim: 1024
    dropout_rate: 0.1
    transformer_activation: glu
model:
  type: LitTransformerModel
  args:
    optimizer:
      type: MADGRAD
      args:
        lr: 0.01
        momentum: 0.9
        weight_decay: 0
        eps: 1.0e-06
    lr_scheduler:
      type: CosineAnnealingLR
      args:
        T_max: 512
    criterion:
      type: CrossEntropyLoss
      args:
        weight: None
        ignore_index: -100
        reduction: mean
    monitor: val_loss
    mapping: sentence_piece
data:
  type: IAMExtendedParagraphs
  args:
    batch_size: 16
    num_workers: 12
    train_fraction: 0.8
    augment: true
callbacks:
- type: ModelCheckpoint
  args:
    monitor: val_loss
    mode: min
- type: EarlyStopping
  args:
    monitor: val_loss
    mode: 

In [1]:
""" tes".t """

' tes".t '

In [2]:
from text_recognizer.networks import CNN, TDS2d

In [3]:
tds2d = TDS2d(**{
    "depth" : 4,
    "tds_groups" : [
      { "channels" : 4, "num_blocks" : 3, "stride" : [2, 2] },
      { "channels" : 32, "num_blocks" : 3, "stride" : [2, 2] },
      { "channels" : 64, "num_blocks" : 3, "stride" : [2, 2] },
      { "channels" : 128, "num_blocks" : 3, "stride" : [2, 1] },
    ],
    "kernel_size" : [5, 7],
    "dropout_rate" : 0.1
  }, input_dim=32, output_dim=128)

In [4]:
tds2d

TDS2d(
  (tds): Sequential(
    (0): Conv2d(1, 16, kernel_size=[5, 7], stride=[2, 2], padding=(2, 3))
    (1): ReLU(inplace=True)
    (2): Dropout(p=0.1, inplace=False)
    (3): InstanceNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
    (4): TDSBlock2d(
      (conv): Sequential(
        (0): Conv3d(4, 4, kernel_size=(1, 5, 7), stride=(1, 1, 1), padding=(0, 2, 3))
        (1): ReLU(inplace=True)
        (2): Dropout(p=0.1, inplace=False)
      )
      (mlp): Sequential(
        (0): Linear(in_features=16, out_features=16, bias=True)
        (1): ReLU(inplace=True)
        (2): Dropout(p=0.1, inplace=False)
        (3): Linear(in_features=16, out_features=16, bias=True)
        (4): Dropout(p=0.1, inplace=False)
      )
      (instance_norm): ModuleList(
        (0): InstanceNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
        (1): InstanceNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
      )
    )


In [5]:
summary(tds2d, (1, 28, 952), device="cpu", depth=3)

Layer (type:depth-idx)                        Output Shape              Param #
├─Sequential: 1-1                             [-1, 512, 2, 119]         --
|    └─Conv2d: 2-1                            [-1, 16, 14, 476]         576
|    └─ReLU: 2-2                              [-1, 16, 14, 476]         --
|    └─Dropout: 2-3                           [-1, 16, 14, 476]         --
|    └─InstanceNorm2d: 2-4                    [-1, 16, 14, 476]         32
|    └─TDSBlock2d: 2-5                        [-1, 16, 14, 476]         --
|    |    └─Sequential: 3-1                   [-1, 4, 4, 14, 476]       564
|    |    └─Sequential: 3-2                   [-1, 476, 14, 16]         544
|    └─TDSBlock2d: 2-6                        [-1, 16, 14, 476]         --
|    |    └─Sequential: 3-3                   [-1, 4, 4, 14, 476]       564
|    |    └─Sequential: 3-4                   [-1, 476, 14, 16]         544
|    └─TDSBlock2d: 2-7                        [-1, 16, 14, 476]         --
|    |    └─Seq

Layer (type:depth-idx)                        Output Shape              Param #
├─Sequential: 1-1                             [-1, 512, 2, 119]         --
|    └─Conv2d: 2-1                            [-1, 16, 14, 476]         576
|    └─ReLU: 2-2                              [-1, 16, 14, 476]         --
|    └─Dropout: 2-3                           [-1, 16, 14, 476]         --
|    └─InstanceNorm2d: 2-4                    [-1, 16, 14, 476]         32
|    └─TDSBlock2d: 2-5                        [-1, 16, 14, 476]         --
|    |    └─Sequential: 3-1                   [-1, 4, 4, 14, 476]       564
|    |    └─Sequential: 3-2                   [-1, 476, 14, 16]         544
|    └─TDSBlock2d: 2-6                        [-1, 16, 14, 476]         --
|    |    └─Sequential: 3-3                   [-1, 4, 4, 14, 476]       564
|    |    └─Sequential: 3-4                   [-1, 476, 14, 16]         544
|    └─TDSBlock2d: 2-7                        [-1, 16, 14, 476]         --
|    |    └─Seq

In [6]:
t = torch.randn(2,1, 28, 952)

In [7]:
tds2d(t).shape

torch.Size([2, 119, 128])

In [9]:
cnn = CNN().cuda()

In [ ]:
i = nn.Sequential(nn.Conv2d(1,1,1,1))

In [ ]:
nn.Sequential(i,i)

In [ ]:
cnn(t).shape

In [ ]:
from text_recognizer.networks.vqvae import Encoder, Decoder, VQVAE

In [ ]:
vqvae = VQVAE(1, [32, 128, 128, 256], [4, 4, 4, 4], [2, 2, [1, 2], [1, 2]], 2, 32, 256, [[6, 119], [7, 238]])

In [ ]:
t = torch.randn(2, 1, 28, 952)

In [ ]:
x, l = vqvae(t)

In [ ]:
5 * 59 / 10

In [ ]:
x.shape

In [ ]:
summary(vqvae, (1, 28, 952), device="cpu", depth=3)

In [ ]:
up = nn.Upsample([4, 59])

In [ ]:
up(tt).shape

In [ ]:
tt.shape

In [ ]:
class GEGLU(nn.Module):
    def __init__(self, dim_in, dim_out):
        super().__init__()
        self.proj = nn.Linear(dim_in, dim_out * 2)

    def forward(self, x):
        x, gate = self.proj(x).chunk(2, dim = -1)
        return x * F.gelu(gate)

In [ ]:
e = GEGLU(256, 2048)

In [ ]:
e(t).shape

In [ ]:
emb = nn.Embedding(56, 256)

In [ ]:
with torch.no_grad():
    e = emb(torch.Tensor([55]).long())

In [ ]:
from einops import repeat

In [ ]:
ee = repeat(e, "() n -> b n", b=16)

In [ ]:
emb.device

In [ ]:
ee

In [ ]:
ee.shape

In [ ]:
t = torch.randn(16, 10, 256)

In [ ]:
t.shape

In [ ]:
t = torch.cat((ee.unsqueeze(1), t, ee.unsqueeze(1)), dim=1)

In [ ]:
t.shape

In [ ]:
e.shape

In [ ]:
from text_recognizer.networks.residual_network import IdentityBlock, ResidualBlock, BasicBlock, BottleNeckBlock, ResidualLayer, ResidualNetwork, ResidualNetworkEncoder

In [ ]:
from text_recognizer.networks import WideResidualNetwork

In [ ]:
wr = WideResidualNetwork(
            in_channels= 1,
            num_classes= 80,
            in_planes=64,
            depth=10,
            num_layers=4,
            width_factor=2,
            num_stages=[64, 128, 256, 256],
            dropout_rate= 0.1,
            activation= "SELU",
            use_decoder= False,
)

In [ ]:
from torchsummary import summary

In [ ]:
backbone = ResidualNetworkEncoder(1, [64, 65, 66, 67, 68], [2, 2, 2, 2, 2])

In [ ]:
summary(backbone, (1, 28, 952), device="cpu", depth=3)

In [ ]:
        backbone = nn.Sequential(
            *list(wr.children())[:][:]
        )


In [ ]:
backbone

In [ ]:
summary(wr, (1, 28, 952), device="cpu", depth=3)

In [ ]:
a = torch.rand(1, 1, 28, 952)

In [ ]:
b = wr(a)

In [ ]:
from einops import rearrange

In [ ]:
b = rearrange(b, "b c h w -> b w c h")

In [ ]:
c = nn.AdaptiveAvgPool2d((None, 1))

In [ ]:
d = c(b)

In [ ]:
d.shape

In [ ]:
d.squeeze(3).shape

In [ ]:
b.shape

In [ ]:
from torch import nn

In [ ]:
32 + 64

In [ ]:
3 * 112

In [ ]:
col_embed = nn.Parameter(torch.rand(1000, 256 // 2))

In [ ]:
W, H = 196, 4

In [ ]:
col_embed[:W].unsqueeze(0).repeat(H, 1, 1).shape

In [ ]:
col_embed[:H].unsqueeze(1).repeat(1, W, 1).shape

In [ ]:
           torch.cat(
                [
                    col_embed[:W].unsqueeze(0).repeat(H, 1, 1),
                    col_embed[:H].unsqueeze(1).repeat(1, W, 1),
                ],
                dim=-1,
            ).unsqueeze(0).shape

In [ ]:
4 * 196

In [ ]:
target = torch.tensor([1,1,12,1,1,1,1,1,9,9,9,9,9,9])

In [ ]:
torch.nonzero(target == 9, as_tuple=False)[0].item()

In [ ]:
target[:9]

In [ ]:
np.inf

In [ ]:
from text_recognizer.networks.transformer.positional_encoding import PositionalEncoding

In [ ]:
plt.figure(figsize=(15, 5))
pe = PositionalEncoding(20, 0)
y = pe.forward(torch.zeros(1, 100, 20))
plt.plot(np.arange(100), y[0, :, 4:8].data.numpy())
plt.legend(["dim %d"%p for p in [4,5,6,7]])
None

In [ ]:
from text_recognizer.networks.densenet import DenseNet,_DenseLayer,_DenseBlock

In [ ]:
dnet = DenseNet(12, (6, 12, 10), 1, 24, 80, 4, 0, True)

In [ ]:
216 / 8

In [ ]:
summary(dnet, (1, 28, 952), device="cpu", depth=3)

In [ ]:
        backbone = nn.Sequential(
            *list(dnet.children())[:][:-4]
        )

In [ ]:
backbone

In [ ]:
from text_recognizer.networks import WideResidualNetwork

In [ ]:
w = WideResidualNetwork(
        in_channels = 1,
        in_planes = 32,
        num_classes = 80,
        depth = 10,
        width_factor = 1,
        dropout_rate = 0.0,
        num_layers = 5,
        activation = "relu",
        use_decoder = False,)

In [ ]:
summary(w, (1, 28, 952), device="cpu", depth=2)

In [ ]:
sz= 5

In [ ]:
mask = torch.triu(torch.ones(sz, sz), 1)
mask = mask.masked_fill(mask==1, float('-inf'))

In [ ]:

h = torch.rand(1, 256, 10, 10)

In [ ]:
h.flatten(2).permute(2, 0, 1).shape

In [ ]:
h.flatten(2).permute(2, 0, 1).shape

In [ ]:
mask


In [ ]:
pred = torch.Tensor([1,21,2,45,31, 81, 1, 79, 79, 79, 2,1,1,1,1, 81, 1, 79, 79, 79, 1,1,1,1,1, 81, 79, 79, 79, 79]).long()
target = torch.Tensor([1,1,1,1,1, 81, 79, 79, 79, 79, 1,1,1,1,1, 81, 79, 79, 79, 79, 1,1,1,1,1, 81, 79, 79, 79, 79]).long()

In [ ]:
mask = (target != 79)

In [ ]:
mask

In [ ]:
pred * mask

In [ ]:
target * mask

In [ ]:
from text_recognizer.models.metrics import accuracy

In [ ]:
pad_indcies = torch.nonzero(target == 79, as_tuple=False)

In [ ]:
t1 = torch.nonzero(target == 81, as_tuple=False).squeeze(1)

In [ ]:
target.shape[0]

In [ ]:
t2 = torch.arange(10, target.shape[0] + 1, 10)

In [ ]:
t2

In [ ]:
for start, stop in zip(t1, t2):
    pred[start+1:stop] = 79

In [ ]:
pred

In [ ]:
[pred[start+1:stop] = 79 for start, stop in zip(t1, t2)]

In [ ]:
pad_indcies

In [ ]:
pred[pad_indcies:pad_indcies] = 79

In [ ]:
pred.shape

In [ ]:
target.shape

In [ ]:
accuracy(pred, target)

In [ ]:
acc = (pred == target).sum().float() / target.shape[0]

In [ ]:
acc